In [ ]:
Phi = function('Phi')
F = function('F')
F_r = function('F_r')
A_r = function('A_r')
maxima_calculus('algebraic: true;')
var('u x t tau rho')
var('r', domain='integer')

In [ ]:
subs_dict = {
    A_r(x,1) : F(x),
    Phi(F(x)): F(x)/x,
}

In [ ]:
A.<Z> = AsymptoticRing('Z^QQ', SR, default_prec=8)

In [ ]:
implicit_equation = A_r(x,u) == x * Phi(A_r(x,u)) + (1 - 1/u)*F_r(x*u)

In [ ]:
[phi_diff1_eq] = (F(x) == x*Phi(F(x))).diff(x, 1).solve(Phi(t).diff(t,1)(t=F(x)))
phi_diff1_eq = phi_diff1_eq.subs(subs_dict)
subs_dict[phi_diff1_eq.lhs()] = phi_diff1_eq.rhs()
phi_diff1_eq.show()

In [ ]:
[phi_diff2_eq] = (F(x) == x*Phi(F(x))).diff(x, 2).solve(Phi(t).diff(t,2)(t=F(x)))
phi_diff2_eq = phi_diff2_eq.subs(subs_dict).simplify_rational()
subs_dict[phi_diff2_eq.lhs()] = phi_diff2_eq.rhs()
phi_diff2_eq.show()

In [ ]:
A_r_diff_u1 = implicit_equation.diff(u)(u=1)\
    .solve(A_r(x,u).diff(u,1)(u=1))[0].subs(subs_dict)\
    .simplify_rational().rhs()
A_r_diff_u1.show()

In [ ]:
A_r_diff_u2 = implicit_equation.diff(u,2)(u=1)\
    .solve(A_r(x,u).diff(u,2)(u=1))[0].subs(subs_dict)\
    .subs({A_r(x,u).diff(u,1)(u=1): A_r_diff_u1})\
    .simplify_rational().rhs()
A_r_diff_u2.expand().show()

In [ ]:
var('f0 f1 f2 fr0 fr1 fr2')

In [ ]:
def F_r_expansion(offset=0, precision=3):
    return sum([(-1)^k * rho^k * F_r(x).diff(x, k+offset)(x=rho) 
                / k.factorial() * Z^(-k) 
                for k in srange(0, precision+1)])\
                + O(Z^(-(precision+1)))

In [ ]:
F_r_expansion(offset=0).show()

In [ ]:
%%time
F_expansion = asymptotic_expansions\
                .ImplicitExpansion(Z, phi=Phi, tau=tau, precision=5)
F_expansion = F_expansion.map_coefficients(lambda ex: ex.subs({
    Phi(t).diff(t)(t=tau): Phi(tau)/tau
}).simplify_rational().subs({
    Phi(tau) : tau/rho
}).simplify_rational())
F_expansion.show()

In [ ]:
var('alpha beta gamma')
coefficients_dict = {
    alpha: -F_expansion.monomial_coefficient(Z^(-1/2)),
    beta: F_expansion.monomial_coefficient(Z^(-1)),
    gamma: F_expansion.monomial_coefficient(Z^(-3/2)),
}
F_expansion_stub = tau - alpha*Z^(-1/2) + beta*Z^(-1) + gamma*Z^(-3/2) + O(Z^(-2))
F_diff1_expansion_stub = alpha/(2*rho)*Z^(1/2) -beta/rho - 3*gamma/(2*rho)*Z^(-1/2) + O(Z^(-1))
F_diff2_expansion_stub = alpha/(4*rho^2) * Z^(3/2) + 3*gamma/(4*rho^2)*Z^(1/2) + O(Z^0)

In [ ]:
A_r_diff_u1_func = fast_callable(A_r_diff_u1.subs({
    F(x): f0,
    F(x).diff(x,1): f1,
    F_r(x): fr0,
    F_r(x).diff(x,1): fr1
}), vars=[x, f0, f1, fr0])
A_r_diff_u1_expansion = A_r_diff_u1_func(rho*(1 - Z^(-1)), 
                                         F_expansion_stub, 
                                         F_diff1_expansion_stub, 
                                         F_r_expansion(offset=0, precision=3))

In [ ]:
fmom1_asy = (A_r_diff_u1_expansion._singularity_analysis_('n', zeta=rho) / F_expansion_stub._singularity_analysis_('n', zeta=rho))\
    .map_coefficients(lambda t: t.simplify_rational())
fmom1_asy.show()

In [ ]:
A_r_diff_u2_func = fast_callable(A_r_diff_u2.subs({
    F(x): f0,
    F(x).diff(x,1): f1,
    F(x).diff(x,2): f2,
    F_r(x): fr0,
    F_r(x).diff(x,1): fr1
}), vars=[x, f0, f1, f2, fr0, fr1])
A_r_diff_u2_expansion = A_r_diff_u2_func(
    rho*(1 - Z^(-1)), F_expansion_stub, F_diff1_expansion_stub,
    F_diff2_expansion_stub, F_r_expansion(offset=0, precision=4),
    F_r_expansion(offset=1, precision=4)
)

In [ ]:
fmom2_asy = (A_r_diff_u2_expansion._singularity_analysis_('n', zeta=rho) / F_expansion_stub._singularity_analysis_('n', zeta=rho))\
    .map_coefficients(lambda t: t.simplify_rational())
fmom2_asy.show()

In [ ]:
variance_asy = (fmom2_asy + fmom1_asy - fmom1_asy^2).map_coefficients(lambda t: t.simplify_rational())
variance_asy.show()